# Import

In [ ]:
import torch

In [ ]:
import os
import glob
import time
import random
import numpy as np
import scipy as sp
import pandas as pd
print ("Numpy:",np.__version__ , "Scipy:",sp.__version__, "Pandas",pd.__version__)

# import tensorflow as tf
# from tensorflow.keras import datasets, layers, Sequential, Model, activations, initializers, regularizers, constraints
# from tensorflow.keras.layers import InputSpec
# import tensorflow.keras.backend as K
# from tensorflow.keras.utils import to_categorical
# from tensorflow.python.compiler.tensorrt import trt_convert as trt
# print ("TensorFlow:",tf.__version__)
# # import horovod.tensorflow as hvd
# print ("GPU List:", tf.config.list_physical_devices('GPU'))

import torch
# import torchmetrics
import pytorch_lightning as pl
from pytorch_lightning import Trainer
from pytorch_lightning.callbacks import ModelCheckpoint, EarlyStopping

# from pytorch_lightning import loggers as pl_loggers
# from pytorch_lightning.loggers import MLFlowLogger
# from pytorch_lightning.loggers import NeptuneLogger
import wandb
from pytorch_lightning.loggers import WandbLogger

# from pytorch_lightning.plugins import CheckpointIO
# from pytorch_lightning.strategies import SingleDeviceStrategy
import torchvision
import torchvision.transforms as transforms
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torch.cuda as cuda
from torch.utils.data import TensorDataset, Dataset, DataLoader
from torch.utils.tensorboard import SummaryWriter
from torchsummary import summary
from datetime import datetime
print ("Pytorch Normal:", torch.__version__)
print ("Pytorch Lightning:", pl.__version__)

import pyspark as ps
from pyspark.mllib.stat import Statistics
from pyspark.sql import SparkSession

# from mlflow import log_metric, log_param, log_artifacts

from IPython import display
# from matplotlib import pyplot as plt
# import matplotlib.cm as cm
# from matplotlib.colors import ListedColormap
import seaborn as sns
import plotly.express as px
import plotly.figure_factory as ff
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import MinMaxScaler
from sklearn.decomposition import PCA
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from sklearn.datasets import make_friedman1
from sklearn.datasets import make_friedman2
from sklearn.datasets import make_friedman3
# from sklearn.preprocessing import MinMaxScaler
# from sklearn.cluster import AgglomerativeClustering
# from sklearn.preprocessing import StandardScaler
# from sklearn.cluster import KMeans
# from sklearn.utils import resample
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import normalize
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import cross_validate
from sklearn import metrics
from IPython.display import clear_output

from math import *

from ripser import ripser
from ripser import Rips
from persim import plot_diagrams

# import cv2
# import PIL
# import imageio
# import pickle

# Data Visualization

In [ ]:
df_deas = pd.read_csv("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_1/DEAS/df_deas_3.csv", index_col=0)
df_share = pd.read_csv("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_1/SHARE/df_gv_health_7.csv", index_col=0)
print(df_deas.shape, df_share.shape)
print(df_deas.columns)
print(df_share.columns)

In [ ]:
df_deas = df_deas[df_deas["ic505"]>100]

In [ ]:
px.imshow(df_share.corr(), zmin=-1, zmax=1)
# px.imshow(df_deas.corr(), zmin=-1, zmax=1)

# Dataset creation

In [ ]:
df_pseudo_share = pd.DataFrame(columns=[
           "age", # age info year of birth# added for dataselection
           "bmi",
           "sphus","sphus2", # us version of self reported activity
           "chronic2w8","chronicw8c", # numbner of chronic diseasae (integer) , wheather one has more than one chronic diseaese (binary)
           "numeracy2", "orienti", "cf008tot","cf016tot", # cognitive fuction tests ( numeracy score, orientation to date, short term memory, long term memory test)
           'euro1', 'euro2', 'euro3', 'euro4', 'euro5', 'euro6','euro7', 'euro8', 'euro9', 'euro10', 'euro11', 'euro12', # Mental health (depression, pessimism, suicidality, guilt, sleep, interest, irritability, appetite, fatigue, concentration,enjoyment, tearfulness)
           'loneliness', #loneliness
           "gali", #limitation to activities
           "mobility","mobilit2", "mobilit3", "adl","adl2", "iadl", "iadl2", # ability and limitatiopn to motor mobility
           ])

In [ ]:
rng = np.random.default_rng()
c1 = rng.random()
c2 = rng.random()
c3 = rng.random()
c4 = rng.random()
c5 = rng.random()


b1 = rng.integers(low = 0, high = 7)
b2 = rng.integers(low = 1, high = 7)
b3 = rng.integers(low = 0, high = 5)

n1 = rng.integers(low = 1, high = 3)
n2 = rng.integers(low = 1, high = 3)
n3 = rng.integers(low = 1, high = 2)
n4 = rng.integers(low = 1, high = 2)

print (c1,c2,c3,c4,c5,'\n', b1,b2,b3, '\n', n1,n2,n3,n4 )

In [ ]:
df_pseudo_share["age"]= df_deas["ic2a"]
df_pseudo_share["age_norm"]= df_pseudo_share['age'].apply(lambda x: (x - df_pseudo_share['age'].min()) / (df_pseudo_share['age'].max() - df_pseudo_share['age'].min()))
df_pseudo_share["bmi"]= df_deas["ic506"]/((df_deas["ic505"]/100)**2)
df_pseudo_share["sphus"]= pd.qcut(
    ((df_pseudo_share["age_norm"])*0.2
     +0.9* df_deas[["ic518a1","ic518a2", "ic518a3", "ic518a4", "ic518a5", "ic518a6", "ic518a7", "ic518a8", "ic518a9", "ic518a10", "ic518a11", "ic518a12", "ic518a13", "ic518a14", "ic518a15", "ic518a16",
                    "ic518a17", "ic518a18", "ic518a19"]].sum(axis=1)
     + c1), q= [0,0.04,0.2,0.6,0.9,1.0], labels=False) +1
df_pseudo_share["sphus2"] = df_pseudo_share["sphus"].apply(lambda x: 0 if x in [0, 1] else 1)
df_pseudo_share["chronicw8c"] = df_deas[["ic518a1","ic518a2", "ic518a3", "ic518a4", "ic518a5", "ic518a6", "ic518a7", "ic518a8", "ic518a9", "ic518a10", "ic518a11", "ic518a12", "ic518a13", "ic518a14", "ic518a15", "ic518a16", "ic518a17",
                                         "ic518a18", "ic518a19"]].sum(axis=1)
df_pseudo_share["chronic2w8"] = df_pseudo_share["chronicw8c"].apply(lambda x: 0 if x <=0 else 1)
df_pseudo_share["numeracy2"] = pd.qcut( (df_pseudo_share["age_norm"]**n1 + b1*(df_deas.zzgscore_17/(df_deas.zzfscore_17+c2)) + b2*(df_deas.zzgscore_17/(df_deas.zzfscore_17+c2))**n2)  ,
                                    q= [0,0.01,0.03,0.05,0.12,0.3,1.0], labels=False)
df_pseudo_share["orienti"] = pd.qcut( (df_pseudo_share["age_norm"]**n3 + b3*(df_deas.zzgscore_17/(df_deas.zzfscore_17+c4))**n4)  ,
                                     q = [0,0.001,0.002,0.01,0.12,1], labels=False)
df_pseudo_share["cf008tot"] = pd.qcut( (df_pseudo_share["age_norm"]**n1 + b1*(df_deas.zzgscore_17/(df_deas.zzfscore_17+c2)) + b2*(df_deas.zzgscore_17)**n2 + 10*c5)
                                      , q = [0,0.004,0.007,0.02,0.07,0.19,0.4,0.65,0.86,0.96,0.99,1], labels=False)
df_pseudo_share["cf016tot"] = pd.qcut( (df_pseudo_share["age_norm"]**n1 + b1*(df_deas.zzgscore_17/(df_deas.zzfscore_17+c2)) + b2*(df_deas.zzgscore_17)**n2 - 2*c5)  , 11, labels=False)
df_pseudo_share["euro1"] = df_deas.ic504_4.apply(lambda x: 0 if x <= 1 else 1) #depression
df_pseudo_share["euro2"] = df_deas.ic504_6.apply(lambda x: 0 if x <= 1 else 1) #pessimism
df_pseudo_share["euro3"] = df_deas.ic504_15.apply(lambda x: 0 if x <= 1 else 1) #suicidality
df_pseudo_share["euro4"] = df_deas.ic504_2.apply(lambda x: 0 if x <= 2 else 1) # guilt
df_pseudo_share["euro5"] = df_deas.ic504_8.apply(lambda x: 0 if x <= 2 else 1) #sleep
df_pseudo_share["euro6"] = (df_deas.ic504_1+df_deas.ic504_5).apply(lambda x: 0 if x <= 3 else 1) # interest
df_pseudo_share["euro7"] = df_deas.ic504_1.apply(lambda x: 0 if x <= 2 else 1) # irritability
df_pseudo_share["euro8"] = df_deas.ic504_7.apply(lambda x: 0 if x <= 2 else 1) # appetite
df_pseudo_share["euro9"]  = df_deas.ic504_5.apply(lambda x: 0 if x <= 2 else 1)  #fatigue
df_pseudo_share["euro10"] = df_deas.ic504_3.apply(lambda x: 0 if x <= 2 else 1) # concentration
df_pseudo_share["euro11"] = df_deas.ic504_12.apply(lambda x: 1 if x <= 1 else 0) # enjoyment
df_pseudo_share["euro12"] = df_deas.ic504_13.apply(lambda x: 0 if x <= 1 else 1) # tearfulness
df_pseudo_share["loneliness"]  = df_deas.ic504_11*2 + 1#.apply(lambda x: 0 if x <= 1 else 1)
df_pseudo_share["gali"]  = df_deas.id36_3.apply(lambda x: 0 if x==2 else 1)
df_pseudo_share["mobility"] =15 - df_deas[["ic511_6","ic511_10","ic511_11","ic511_12","ic511_13"]].sum(axis=1)
df_pseudo_share["mobilit2"] = df_pseudo_share["mobility"].apply(lambda x: 0 if x<=0 else 1)
df_pseudo_share["mobilit3"] = df_pseudo_share["mobility"].apply(lambda x: 0 if x<=1 else 1)
df_pseudo_share["adl"] = (11 - df_deas[["ic511_2","ic511_3","ic511_5","ic511_6","ic511_10"]].sum(axis=1)).apply (lambda x: 0 if x <= 0 else x)
df_pseudo_share["adl2"] = df_pseudo_share["adl"].apply (lambda x: 0 if x <= 0 else 1)
df_pseudo_share["iadl"] = (14 - df_deas[["ic511_1","ic511_4","ic511_7","ic511_8","ic511_9"]].sum(axis=1)).apply (lambda x: 0 if x <= 0 else x)
df_pseudo_share["iadl2"] = df_pseudo_share["iadl"].apply (lambda x: 0 if x <= 1 else 1)

df_pseudo_share = df_pseudo_share.drop(columns="age_norm")

# Visual Camparison

In [ ]:
df_emergency_psedo_share= pd.read_csv("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/df_pseudo_share_norm.csv", index_col= 0)

In [ ]:
fig = go.Figure()
fig.add_trace(go.Heatmap(z=df_share.corr(), colorscale='Puor', showscale=False, zmin=-1, zmax=1, ))
fig.add_trace(go.Heatmap(z=df_emergency_psedo_share.corr(), colorscale='Puor', showscale=True, zmin=-1, zmax=1, xaxis='x2', yaxis='y2'))
fig.update_layout(
    title='Corr',
    xaxis=dict(domain=[0, 0.45]),
    yaxis=dict(domain=[0, 1]),
    xaxis2=dict(domain=[0.55, 1]),
    yaxis2=dict(domain=[0, 1],showticklabels=False)
)

fig.show()


In [ ]:
for col in df_pseudo_share.columns.to_list() :
    fig1 = px.histogram(df_share[str(col)], histnorm="probability")
    fig2 = px.histogram(df_pseudo_share[str(col)], histnorm="probability")
    fig = make_subplots(rows=1, cols=2, subplot_titles=('share', 'pseudo_share'))
    fig.add_trace(fig1.data[0], row=1, col=1)
    fig.add_trace(fig2.data[0], row=1, col=2)
    fig.update_layout(title_text=str(col))
    fig.show()
    # time.sleep(1)
    # clear_output()

In [ ]:
for col in df_pseudo_share.columns.to_list() :
    fig1 = px.histogram(df_share[str(col)], histnorm="probability")
    fig2 = px.histogram(df_pseudo_share[str(col)], histnorm="probability")
    fig = make_subplots(rows=1, cols=2, subplot_titles=('share', 'pseudo_share'))
    fig.add_trace(fig1.data[0], row=1, col=1)
    fig.add_trace(fig2.data[0], row=1, col=2)
    fig.update_layout(title_text=str(col))
    fig.show()
    time.sleep(1)
    clear_output()

In [ ]:
n_components = 3
pca = PCA(n_components=n_components)
components = pca.fit_transform((df_share))

fig = px.scatter_matrix(
    components,
    color=df_share.bmi,
    # labels=anno_mouse_2.Sample_ID,
    # symbol=anno_mouse_2.Material,
    dimensions=range(n_components),
    # title=f'Total Explained Variance: {total_var:.2f}%',
)
fig.update_traces(diagonal_visible=False)
fig.show()

In [ ]:
n_components = 3
pca = PCA(n_components=n_components)
components = pca.fit_transform((df_pseudo_share))

fig = px.scatter_matrix(
    components,
    color=df_pseudo_share.bmi,
    # labels=anno_mouse_2.Sample_ID,
    # symbol=anno_mouse_2.Material,
    dimensions=range(n_components),
    # title=f'Total Explained Variance: {total_var:.2f}%',
)
fig.update_traces(diagonal_visible=False)
fig.show()

## predicted phy inactivity

In [ ]:
fold = 1
testset = pd.read_csv("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ScienceReseaech/Share/Prepro/centralized/"+str(fold)+"/test.csv", sep=',')
trainset = pd.read_csv("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ScienceReseaech/Share/Prepro/centralized/"+str(fold)+"/train.csv", sep=',')
x_train = trainset.drop(columns='phactiv')
x_test = testset.drop(columns='phactiv')
y_train = trainset["phactiv"]
y_test = testset["phactiv"]
# print(y_test)
clf = RandomForestClassifier()
clf.fit(x_train, y_train)
print ( "test_Acc", clf.score(x_test, y_test) , "test_AUROC :", metrics.roc_auc_score( y_test, clf.predict(x_test)) )


In [ ]:
df_share["phactiv"] =clf.predict(df_share.drop(columns="age"))
df_pseudo_share["phactiv"] =clf.predict(df_pseudo_share.drop(columns="age"))

In [ ]:
n_components = 3
pca = PCA(n_components=n_components)
components = pca.fit_transform((df_share.drop(columns="phactiv")))

fig = px.scatter_matrix(
    components,
    color=df_share.bmi,
    # labels=df_share.phactiv,
    symbol=df_share.phactiv,
    dimensions=range(n_components),
    # title=f'Total Explained Variance: {total_var:.2f}%',
)
fig.update_traces(diagonal_visible=False)
fig.show()

In [ ]:
n_components = 3
pca = PCA(n_components=n_components)
components = pca.fit_transform((df_pseudo_share.drop(columns="phactiv")))

fig = px.scatter_matrix(
    components,
    color=df_pseudo_share.bmi,
    # labels=df_pseudo_share.phactiv,
    symbol=df_pseudo_share.phactiv,
    dimensions=range(n_components),
    # title=f'Total Explained Variance: {total_var:.2f}%',
)
fig.update_traces(diagonal_visible=False)
fig.show()

# Normalisation and data split for KTR unshuffled

In [ ]:
df_deas_norm = df_deas.apply(lambda x: (x - x.min()) / (x.max() - x.min()), axis=0)
df_pseudo_share_norm = df_pseudo_share.apply(lambda x: (x - x.min()) / (x.max() - x.min()), axis=0)

In [ ]:
! mkdir /Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled
! mkdir /Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE
! mkdir /Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS

In [ ]:
df_deas.to_csv("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS/df_deas.csv")
df_deas_norm.to_csv("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS/df_pseudo_share_norm.csv")
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS/df_pseudo_share_norm.npy", df_deas_norm.to_numpy())
df_pseudo_share.to_csv("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/df_pseudo_share.csv")
df_pseudo_share_norm.to_csv("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/df_pseudo_share_norm.csv")
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/df_pseudo_share_norm.npy", df_pseudo_share_norm.to_numpy())

In [ ]:
np_deas = np.load('/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS/df_pseudo_share_norm.npy')
np_pseudo_share = np.load('/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/df_pseudo_share_norm.npy')

print (np_pseudo_share.shape, np_deas.shape)

In [ ]:
d_train,d_test, s_train, s_test = train_test_split( np_deas, np_pseudo_share , test_size=0.20, random_state=4)
d_test,d_val, s_test, s_val = train_test_split( d_test, s_test, test_size=0.50, random_state=4)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS/D_train_1.npy", d_train)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS/D_test_1.npy", d_test)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS/D_val_1.npy", d_val)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/S_train_1.npy", s_train)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/S_test_1.npy", s_test)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/S_val_1.npy", s_val)

# Normalisation and data split for KTR shuffled

In [ ]:
np_deas = np.load('/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS/df_pseudo_share_norm.npy')
np_pseudo_share = np.load('/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/df_pseudo_share_norm.npy')
np.random.shuffle(np_deas)
np.random.shuffle(np_pseudo_share)
print (np_pseudo_share.shape, np_deas.shape)

In [ ]:
! mkdir /Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2
! mkdir /Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2/PSEUDO_SHARE
! mkdir /Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2/DEAS

In [ ]:
d_train,d_test, s_train, s_test = train_test_split( np_deas, np_pseudo_share , test_size=0.20, random_state=4)
d_test,d_val, s_test, s_val = train_test_split( d_test, s_test, test_size=0.50, random_state=4)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2/DEAS/D_train_1.npy", d_train)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2/DEAS/D_test_1.npy", d_test)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2/DEAS/D_val_1.npy", d_val)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2/PSEUDO_SHARE/S_train_1.npy", s_train)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2/PSEUDO_SHARE/S_test_1.npy", s_test)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2/PSEUDO_SHARE/S_val_1.npy", s_val)

In [ ]:
fig = go.Figure()
fig.add_trace(go.Heatmap(z=pd.DataFrame(np_deas).corr(), colorscale='Puor', showscale=False, zmin=-1, zmax=1))
fig.add_trace(go.Heatmap(z=pd.DataFrame(np_pseudo_share).corr(), colorscale='Puor', showscale=True, zmin=-1, zmax=1,  xaxis='x2', yaxis='y2'))
fig.update_layout(
    title='Corr',
    xaxis=dict(domain=[0, 0.45]),
    yaxis=dict(domain=[0, 1]),
    xaxis2=dict(domain=[0.55, 1]),
    yaxis2=dict(domain=[0, 1],showticklabels=False)
)

fig.show()

# KTR half-Shuffled ktr data for 2.2

In [ ]:
np_deas = np.load('/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/DEAS/df_pseudo_share_norm.npy')
np_pseudo_share = np.load('/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2_unshuffled/PSEUDO_SHARE/df_pseudo_share_norm.npy')

d_train,d_test, s_train, s_test = train_test_split( np_deas, np_pseudo_share , test_size=0.20, random_state=4)
d_test,d_val, s_test, s_val = train_test_split( d_test, s_test, test_size=0.50, random_state=4)

In [ ]:
np.random.shuffle(d_train)
np.random.shuffle(d_val)
np.random.shuffle(s_train)
np.random.shuffle(s_val)

In [ ]:
!mkdir /Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2.2

In [ ]:
!mkdir /Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2.2/DEAS
!mkdir /Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2.2/PSEUDO_SHARE

In [ ]:
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2.2/DEAS/D_train_2_2.npy", d_train)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2.2/DEAS/D_val_2_2.npy", d_val)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2.2/DEAS/D_test_2_2.npy", d_test)

np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2.2/PSEUDO_SHARE/S_train_2_2.npy", s_train)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2.2/PSEUDO_SHARE/S_val_2_2.npy", s_val)
np.save("/Users/supratim/Library/CloudStorage/OneDrive-Personal/ResearchDataset/KTR/KTR_2.2/PSEUDO_SHARE/S_test_2_2.npy", s_test)
